In [7]:
import pandas as pd
import os
os.chdir(r'C:\Users\lenovo\Desktop')

In [8]:
df1=pd.read_csv('final_reviews.csv')

In [14]:
df1.drop(['rating','work/life','culture/values','career_opp','compensation/ben','senior_mng'], axis=1,inplace=True)

In [15]:
df1

title  \
0                                     Great place to work   
1                               awesome work life balance   
2                                        Employee Centric   
3       Great Company to work for, one of the best in ...   
4                   Nice company to work at all hierarchy   
5                                            Nice Company   
6       Good place to Work - Great policies &amp; bene...   
7                       Good Company, Bad Division (PPBU)   
8                  Adobe India Document Cloud Server Team   
9                             Computer Scientist at Adobe   
10                                       Working at Adobe   
11                                    It's a good company   
12                                           Good Company   
13      A fantastic company to work for. Great work cu...   
14                                    Good for Retirement   
15                       A great place to learn and grow!   
16                              Employee Friendly company   
17                                     Best place to work   
18                              Best Company to work with   
19                                   All play but no work   
20                                              Good.....   
21                                       Best of the Best   
22      Adobe is a nice company but beware of legacy p...   
23         No salary hike for Lateral hires for 2-3 years   
24                                     Work/Life in Adobe   
25                                 Great place to work at   
26                               Good company to with for   
27                                     Amazing Experience   
28                     Member of technical staff at Adobe   
29                   I love being productmanager at Adobe   
...                                                   ...   
165222     Good company to work with competitive salaries   
165223                         Feedback about Wipro Sales   
165224                             Worked for 2 projects.   
165225                                     My Perspective   
165226                             A Place for sycophants   
165227       Poor management and explotation of resource.   
165228  If you work for Wipro for awhile any future jo...   
165229           Open your eyes and learn your weaknesses   
165230   I enjoyed working with Wipro - great experience!   
165231                          Wipro - a place not to be   
165232    Not a good company to work for more than a year   
165233     Wipro - only good for people who play politics   
165234  Good pay master in India .Don't expect much on...   
165235                 A place to grow and make a career.   
165236  Good to work and stay, but not at all good pay...   
165237                          Wipro Technologies Review   
165238  If you need good experience and can put up wit...   
165239  ABSOLUTE NO if you are  in US, a good employer...   
165240  Decent place if you want to learn Global Netwo...   
165241                                   Not really great   
165242                              Good Medical Benefits   
165243                                        Think again   
165244                                               None   
165245                                          My review   
165246                                 Wipro - Programmer   
165247                               Wipro congress party   
165248                     It's not a great place to work   
165249                                               Good   
165250  Co-workers are great to work with, but managem...   
165251                     Project Lead in Wipro Infotech   

                                                     pros  \
0         Employee friendly, Great Culture, Strong Values   
1                              work life balance is great   
2             Employee friendly .Think about their growth   
3          Good work envi

In [16]:
from tqdm import tqdm
tqdm.pandas()

In [17]:
head=['title','pros','cons']

In [23]:
for i in head:
    df1['{}'.format(i)]=df1['{}'.format(i)].astype(str)

In [41]:
import nltk
import re
sentence_re = r'(?:(?:[A-Z])(?:.[A-Z])+.?)|(?:\w+(?:-\w+)*)|(?:\$?\d+(?:.\d+)?%?)|(?:...|)(?:[][.,;"\'?():-_`])'
grammar = r'''
        NBAR:
            {<NN.?>+<RB.?>+}
            {<RB.?>+<NN.?>+}
            {<DT>?<JJ.?|NN.?>*<DT>?<NN.?|JJ.?>*}
            {<V.*|NN.?>*<NN.?|JJ>?<NN.?>*}
        NP:
            {<NBAR><IN><NBAR>}
            {<NBAR>}1
    '''

def fff(text_):
    final_list=[]
    
    from nltk.corpus import stopwords
    stopwords = stopwords.words('english')
    stopwords=set([word for word in stopwords if word not in ['in','no','not','from']])
    
    text_=re.sub('[()]', ' ', text_)
    cons=['and','but','for','nor','or','so','yet','1','2','3','4','5','6','7','8','9']
    for con in cons:
        text_=re.sub(r' {} '.format(con),',',text_)
    a_list = [i for i in re.split(r'([,.])', text_) if i not in ['.',',','',' ']]
    for text in a_list:
        
        chunker = nltk.RegexpParser(grammar)

        toks1 = nltk.regexp_tokenize(text, sentence_re)
        #print(toks1)
        toks=[re.sub('[^A-Za-z]', '', word) for word in toks1]
        toks=[word for word in toks if word!='']
        #print(toks)
        postoks = nltk.tag.pos_tag(toks)
        tree = chunker.parse(postoks)
        
        #print(tree)

        def leaves(tree):
            """Finds NP (nounphrase) leaf nodes of a chunk tree."""
            for subtree in tree.subtrees(filter = lambda t: t.label()=='NP'):
                yield subtree.leaves()

        def normalise(word):
            """Normalises words to lowercase and stems and lemmatizes it."""
            word = word.lower()
            word = re.sub(' +', ' ', word)
            # word = stemmer.stem_word(word) #if we consider stemmer then results comes with stemmed word, but in this case word will not match with comment
            #word = lemmatizer.lemmatize(word)
            return word

        def acceptable_word(word):
            """Checks conditions for acceptable word: length, stopword. We can increase the length if we want to consider large phrase"""
            accepted = bool(2 <= len(word) <= 40
                and word not in stopwords)
            return accepted


        def get_terms(tree):
            for leaf in leaves(tree):
                term = [normalise(w) for w,t in leaf if acceptable_word(w) ]
                term=' '.join(term)
                yield term

        terms = list(get_terms(tree))
        for term in terms:
            if term !='':
                final_list.append(term)
        
    return final_list


In [42]:
for i in head:
    df1['{}_nouns'.format(i)]=df1[i].progress_apply(fff)

  0%|▏                                                                          | 332/165252 [00:10<1:30:15, 30.46it/s]

  1%|█                                                                         | 2278/165252 [01:10<1:02:43, 43.30it/s]

  1%|█▏                                                                          | 2477/165252 [01:15<59:11, 45.83it/s]

  2%|█▏                                                                        | 2586/165252 [01:17<1:14:23, 36.44it/s]

  2%|█▏                                                                        | 2767/165252 [01:23<1:21:54, 33.06it/s]

...

100%|███████████████████████████████████████████████████████████████████████▉| 165142/165252 [2:24:53<00:04, 26.69it/s]

100%|███████████████████████████████████████████████████████████████████████▉| 165171/165252 [2:24:54<00:04, 19.98it/s]

100%|███████████████████████████████████████████████████████████████████████▉| 165201/165252 [2:24:56<00:03, 16.60it/s]

100%|███████████████████████████████████████████████████████████████████████▉| 165207/165252 [2:24:57<00:03, 12.52it/s]

100%|████████████████████████████████████████████████████████████████████████| 165252/165252 [2:25:00<00:00, 18.99it/s]


In [43]:
df1

title  \
0                                     Great place to work   
1                               awesome work life balance   
2                                        Employee Centric   
3       Great Company to work for, one of the best in ...   
4                   Nice company to work at all hierarchy   
5                                            Nice Company   
6       Good place to Work - Great policies &amp; bene...   
7                       Good Company, Bad Division (PPBU)   
8                  Adobe India Document Cloud Server Team   
9                             Computer Scientist at Adobe   
10                                       Working at Adobe   
11                                    It's a good company   
12                                           Good Company   
13      A fantastic company to work for. Great work cu...   
14                                    Good for Retirement   
15                       A great place to learn and grow!   
16                              Employee Friendly company   
17                                     Best place to work   
18                              Best Company to work with   
19                                   All play but no work   
20                                              Good.....   
21                                       Best of the Best   
22      Adobe is a nice company but beware of legacy p...   
23         No salary hike for Lateral hires for 2-3 years   
24                                     Work/Life in Adobe   
25                                 Great place to work at   
26                               Good company to with for   
27                                     Amazing Experience   
28                     Member of technical staff at Adobe   
29                   I love being productmanager at Adobe   
...                                                   ...   
165222     Good company to work with competitive salaries   
165223                         Feedback about Wipro Sales   
165224                             Worked for 2 projects.   
165225                                     My Perspective   
165226                             A Place for sycophants   
165227       Poor management and explotation of resource.   
165228  If you work for Wipro for awhile any future jo...   
165229           Open your eyes and learn your weaknesses   
165230   I enjoyed working with Wipro - great experience!   
165231                          Wipro - a place not to be   
165232    Not a good company to work for more than a year   
165233     Wipro - only good for people who play politics   
165234  Good pay master in India .Don't expect much on...   
165235                 A place to grow and make a career.   
165236  Good to work and stay, but not at all good pay...   
165237                          Wipro Technologies Review   
165238  If you need good experience and can put up wit...   
165239  ABSOLUTE NO if you are  in US, a good employer...   
165240  Decent place if you want to learn Global Netwo...   
165241                                   Not really great   
165242                              Good Medical Benefits   
165243                                        Think again   
165244                                               None   
165245                                          My review   
165246                                 Wipro - Programmer   
165247                               Wipro congress party   
165248                     It's not a great place to work   
165249                                               Good   
165250  Co-workers are great to work with, but managem...   
165251                     Project Lead in Wipro Infotech   

                                                     pros  \
0         Employee friendly, Great Culture, Strong Values   
1                              work life balance is great   
2             Employee friendly .Think about their growth   
3          Good work envi

In [44]:
df1.to_csv('final_reviews_keyphrases.csv')